In [1]:
%load_ext autoreload
%autoreload 2

from warnings import warn

import geodatasets
import geopandas as gpd
import lonboard.geopandas
import numpy as np
from lonboard import PolygonLayer
from mapclassify import classify

In [2]:
%load_ext watermark
%watermark -a 'eli knaap'  -iv

Author: eli knaap

lonboard   : 0.10.3
geodatasets: 2024.8.0
numpy      : 2.0.2
mapclassify: 2.8.1
geopandas  : 1.0.1



In [3]:
gdf = gpd.read_file(geodatasets.get_path("geoda.milwaukee1"))

In [4]:
gdf = gdf.to_crs(gdf.estimate_utm_crs())

In [5]:
gdf = gdf[["HH_INC", "geometry"]]

## Simple Map

In [6]:
gdf.explore()

In [7]:
from lonboard import basemap

gdf.lb.explore(
    tiles="CartoDB Positron",
)

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.Positron: 'https://basemaps.cartocdn.com/gl/positron-gl-style/style.json'>, cu…

## boorish (unclassed :P) choropleth

In [8]:
gdf.explore("HH_INC", tiles="CartoDB Darkmatter")

In [9]:
gdf.lb.explore(
    "HH_INC",
)

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

In [10]:
gdf.assign(catinc=gdf.HH_INC.astype("str")).lb.explore("catinc", categorical=True)

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

## simple classified choropleth

In [11]:
gdf.explore(
    "HH_INC",
    scheme="quantiles",
    k=6,
    cmap="YlOrBr",
)

In [12]:
gdf.lb.explore(
    "HH_INC", cmap="YlOrBr", scheme="quantiles", alpha=0.5, layer_kwargs={"opacity": 1}
)

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

In [13]:
gdf.lb.explore(
    "HH_INC", cmap="YlOrBr", scheme="quantiles", alpha=1, layer_kwargs={"opacity": 0.5}
)

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

### custom classification

In [14]:
classify_kwds = {"bins": [20000, 40000, 800000, 2000000]}

gdf.explore(
    "HH_INC",
    cmap="YlOrBr",
    scheme="user_defined",
    classification_kwds=classify_kwds,
)

In [15]:
gdf.lb.explore(
    "HH_INC",
    cmap="YlOrBr",
    scheme="user_defined",
    classification_kwds=classify_kwds,
)

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

## 3D customized choropleth

not actually intended to be attractive; no analogue in `explore`

In [16]:
gdf.lb.explore(
    "HH_INC",
    cmap="plasma",
    scheme="fisher_jenks",
    k=8,
    elevation="HH_INC",
    elevation_scale=0.1,
    wireframe=True,
    layer_kwargs={
        "get_line_color": "green",
        "auto_highlight": True,
    },
    map_kwargs={
        "view_state": {
            "longitude": -87.84,
            "latitude": 43.13,
            "zoom": 8.8,
            "pitch": 44,
            "bearing": -14,
        }
    },
)

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

## compose with lines and points

In [17]:
linedf = gpd.GeoDataFrame(geometry=gdf.boundary)
linedf["len"] = linedf.length

In [18]:
m = linedf.explore(
    "len", cmap="viridis_r", scheme="quantiles", k=10, tiles="CartoDB Darkmatter"
)
gdf.set_geometry(gdf.centroid).explore(color="magenta", m=m)
m

In [19]:
m = linedf.lb.explore("len", cmap="viridis_r", scheme="quantiles", k=10)
gdf.set_geometry(gdf.centroid).lb.explore(color="magenta", m=m)

# cant do this part unless you use fit_bounds?
m.set_view_state(zoom=10.5, longitude=-87.85, latitude=43.05)
m

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(
/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

## categorical

In [20]:
# random categories
gdf["i"] = gdf.index.values

In [21]:
gdf.explore(
    "i",
    categorical=True,
)

In [22]:
gdf.assign(i=gdf["i"].astype(str)).lb.explore(
    "i",
    # categorical=True,
)

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

In [23]:
gdf.assign(icat=gdf["i"].astype("category")).lb.explore(
    "icat",
    # categorical=True,
)

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

In [24]:
categories = classify(gdf.HH_INC, scheme="quantiles", k=5).yb

In [25]:
# categories that are actually quantiles
gdf["q5"] = categories
gdf["q5"] = gdf["q5"].astype("category")

In [26]:
gdf.explore("q5", categorical=True, cmap="tab20b", tiles="CartoDB Positron")

In [27]:
m = gdf.lb.explore(
    "q5",
    categorical=True,
    cmap="tab20b",
    nan_color=[0, 0, 0, 0],
    tiles="CartoDB Positron",
)
m

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.Positron: 'https://basemaps.cartocdn.com/gl/positron-gl-style/style.json'>, cu…

In [28]:
m = gdf.lb.explore("q5", categorical=True, cmap="RdBu", alpha=0.5)

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


In [29]:
m

Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

## animated choropleth

In [30]:
m = gdf.lb.explore(categorical=True, color="orange")
m

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

In [31]:
m.layers[0].get_fill_color = "blue"

without rerendering the map you can update the color

(this updates *both* maps, including the cell above)

In [32]:
m

Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

In [33]:
from time import sleep

for _ in range(5):
    for color in ["yellow", "red", "blue"]:
        m.layers[0].get_fill_color = color
        sleep(0.3)
    sleep(1)

change color in a timed loop like a gif

In [34]:
from ipywidgets import widget
from mapclassify import classify
from mapclassify.util import get_color_array

In [35]:
def choro(
    vals: np.ndarray, classifier: str, cmap: str, k: int, layer: PolygonLayer
) -> widget:
    layer.get_fill_color = get_color_array(vals, classifier, k=k, cmap=cmap)

In [36]:
from matplotlib import colormaps

In [37]:
m = gdf.lb.explore()
m

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

In [38]:
from mapclassify._classify_API import _classifiers

In [39]:
from ipywidgets import fixed, interact

interact(
    choro,
    vals=fixed(gdf.HH_INC),
    classifier=list(_classifiers.keys()),
    k=range(3, 10),
    cmap=list(colormaps.keys()),
    layer=fixed(m.layers[0]),
)

interactive(children=(Dropdown(description='classifier', options=('boxplot', 'equalinterval', 'fisherjenks', '…

<function __main__.choro(vals: numpy.ndarray, classifier: str, cmap: str, k: int, layer: lonboard._layer.PolygonLayer) -> <module 'ipywidgets.widgets.widget' from '/Users/knaaptime/miniforge3/envs/lonboard/lib/python3.12/site-packages/ipywidgets/widgets/widget.py'>>

In [40]:
gdf.loc[0:200, "HH_INC"] = np.nan

m = gdf.lb.explore(
    "HH_INC",
    cmap="Accent",
    nan_color=[0, 0, 0, 0],
)
m

/Users/knaaptime/Dropbox/projects/lonboard/lonboard/_geoarrow/ops/reproject.py:115: UserWarning: Input being reprojected to EPSG:4326 CRS.
Lonboard is only able to render data in EPSG:4326 projection.
  warnings.warn(


Map(basemap_style=<CartoBasemap.DarkMatter: 'https://basemaps.cartocdn.com/gl/dark-matter-gl-style/style.json'…

In [41]:
import pandas as pd
import geopandas as gpd

In [43]:
pd.read_json?

Signature:
pd.read_json(
    path_or_buf: 'FilePath | ReadBuffer[str] | ReadBuffer[bytes]',
    *,
    orient: 'str | None' = None,
    typ: "Literal['frame', 'series']" = 'frame',
    dtype: 'DtypeArg | None' = None,
    convert_axes: 'bool | None' = None,
    convert_dates: 'bool | list[str]' = True,
    keep_default_dates: 'bool' = True,
    precise_float: 'bool' = False,
    date_unit: 'str | None' = None,
    encoding: 'str | None' = None,
    encoding_errors: 'str | None' = 'strict',
    lines: 'bool' = False,
    chunksize: 'int | None' = None,
    compression: 'CompressionOptions' = 'infer',
    nrows: 'int | None' = None,
    storage_options: 'StorageOptions | None' = None,
    dtype_backend: 'DtypeBackend | lib.NoDefault' = <no_default>,
    engine: 'JSONEngine' = 'ujson',
) -> 'DataFrame | Series | JsonReader'
Docstring:
Convert a JSON string to pandas object.

Parameters
----------
path_or_buf : a valid JSON str, path object or file-like object
    Any valid string path is 

In [48]:
gpd.GeoDataFrame.from_records?

Signature:
gpd.GeoDataFrame.from_records(
    data,
    index=None,
    exclude=None,
    columns=None,
    coerce_float: 'bool' = False,
    nrows: 'int | None' = None,
) -> 'DataFrame'
Docstring:
Convert structured or record ndarray to DataFrame.

Creates a DataFrame object from a structured ndarray, sequence of
tuples or dicts, or DataFrame.

Parameters
----------
data : structured ndarray, sequence of tuples or dicts, or DataFrame
    Structured input data.

    .. deprecated:: 2.1.0
        Passing a DataFrame is deprecated.
index : str, list of fields, array-like
    Field of array to use as the index, alternately a specific set of
    input labels to use.
exclude : sequence, default None
    Columns or fields to exclude.
columns : sequence, default None
    Column names to use. If the passed data do not have names
    associated with them, this argument provides names for the
    columns. Otherwise this argument indicates the order of the columns
    in the result (any names not

In [49]:
import pyogrio

In [56]:
gpd.read_file("https://opendata.sandag.org/resource/bazd-d56k.geojson")

shape_area tier    employment_center_name objectid  \
0   88131318.114257813    4                    Alpine        2   
1   54649776.559570313    4             Vista Village       78   
2   102296846.83300781    3            Chula Vista SW       14   
3   56206348.537109375    3             Scripps Ranch       66   
4     78668472.6796875    1                  Downtown       18   
..                 ...  ...                       ...      ...   
76  41850193.522460938    4                     Poway       58   
77   31895380.49609375    4              Barrio Logan        3   
78   48470991.88671875    4  Encinitas - I-5 Eastward       21   
79  117031818.90722656    2                   La Mesa       34   
80   28111550.81640625    4                   Del Mar       17   

          shape_length                                           geometry  
0    82095.15322401328  MULTIPOLYGON (((-116.74405 32.84907, -116.7443...  
1   57916.638005459696  MULTIPOLYGON (((-117.24236 33.20788, -117.2422...  
2   52437.931103912357  MULTIPOLYGON (((-117.09819 32.60519, -117.0981...  
3   47740.884332771486  MULTIPOLYGON (((-117.11062 32.92042, -117.1106...  
4   58026.057579924069  MULTIPOLYGON (((-117.16377 32.73137, -117.1632...  
..                 ...                                                ...  
76  51842.351941062967  MULTIPOLYGON (((-117.02316 32.96491, -117.0231...  
77  35912.004156518509  MULTIPOLYGON (((-117.14586 32.70331, -117.1455...  
78   50967.32091179234  MULTIPOLYGON (((-117.29424 33.07322, -117.2940...  
79  57661.039387024874  MULTIPOLYGON (((-117.0337 32.75349, -117.03374...  
80  24452.462977115603  MULTIPOLYGON (((-117.26227 32.97125, -117.2623...  

[81 rows x 6 columns]

In [44]:
df = pd.read_json(
    "https://opendata.sandag.org/resource/bazd-d56k.json", orient="records"
)
gdf = gpd.GeoDataFrame(df, geometry=df.the_geom, crs=4326)

TypeError: Input must be valid geometry objects: {'type': 'MultiPolygon', 'coordinates': [[[[-116.744047168183, 32.84907231879], [-116.744330284354, 32.848753740673], [-116.745058067178, 32.848763194866], [-116.745111792755, 32.848763323087], [-116.745330146271, 32.847930699928], [-116.745330076666, 32.847918332237], [-116.745324237613, 32.847748638724], [-116.745306254656, 32.847156765166], [-116.745305991718, 32.847110042779], [-116.745301221983, 32.846841057663], [-116.745296748081, 32.846624636133], [-116.745294733469, 32.846555933268], [-116.745292127265, 32.846382104131], [-116.745281847418, 32.846001829378], [-116.745275312631, 32.845708459852], [-116.745283700019, 32.845173854176], [-116.745283015649, 32.845052237647], [-116.745282909321, 32.845033342564], [-116.745276620274, 32.844494329521], [-116.745257439994, 32.843400182825], [-116.745257389733, 32.843391250603], [-116.745252877447, 32.843167957221], [-116.7452419086, 32.842086489107], [-116.745220598188, 32.841481572863],

In [57]:
from geosnap import DataStore

DataStore().lodes_codebook()

OMP: Info #276: omp_set_nested routine deprecated, please use omp_set_max_active_levels instead.


name    variable    type  \
0             total_employees        C000    Num    
1          employees_under_30        CA01    Num    
2             employees_30_54        CA02    Num    
3            employees_55plus        CA03    Num    
4         earnings_under_1250        CE01    Num    
5          earnings_1251_3333        CE02    Num    
6          earnings_over_3333        CE03    Num    
7                    naics_11       CNS01    Num    
8                    naics_21       CNS02    Num    
9                    naics_22       CNS03    Num    
10                   naics_23       CNS04    Num    
11                naics_31_33       CNS05    Num    
12                   naics_42       CNS06    Num    
13                naics_44_45       CNS07    Num    
14                naics_48_49       CNS08    Num    
15                   naics_51       CNS09    Num    
16                   naics_52       CNS10    Num    
17                   naics_53       CNS11    Num    
18                   naics_54       CNS12    Num    
19                   naics_55       CNS13    Num    
20                   naics_56       CNS14    Num    
21                   naics_61       CNS15    Num    
22                   naics_62       CNS16    Num    
23                   naics_71       CNS17    Num    
24                   naics_72       CNS18    Num    
25                   naics_81       CNS19    Num    
26                   naics_92       CNS20    Num    
27            employees_white        CR01    Num    
28            employees_black        CR02    Num    
29  employees_native_american        CR03    Num    
30            employees_asian        CR04    Num    
31      employees_hawaiian_pi        CR05    Num    
32    employees_twoplus_races        CR07    Num    
33     employees_not_hispanic        CT01    Num    
34         employees_hispanic        CT02    Num    
35             education_lths        CD01    Num    
36               education_hs        CD02    Num    
37     education_some_college        CD03    Num    
38        education_bachelors        CD04    Num    
39             employees_male        CS01    Num    
40           employees_female        CS02    Num    
41                create_date  createdate  Char8    

                                          description  
0                               Total number of jobs   
1     Number of jobs for workers age 29 or younger14   
2          Number of jobs for workers age 30 to 5414   
3       Number of jobs for workers age 55 or older14   
4   Number of jobs with earnings $1250/month or less   
5   Number of jobs with earnings $1251/month to $3...  
6   Number of jobs with earnings greater than $333...  
7   Number of jobs in NAICS sector 11 (Agriculture...  
8   Number of jobs in NAICS sector 21 (Mining, Qua...  
9      Number of jobs in NAICS sector 22 (Utilities)   
10  Number of jobs in NAICS sector 23 (Construction)   
11  Number of jobs in NAICS sector 31-33 (Manufact...  
12  Number of jobs in NAICS sector 42 (Wholesale T...  
13  Number of jobs in NAICS sector 44-45 (Retail T...  
14  Number of jobs in NAICS sector 48-49 (Transpor...  
15   Number of jobs in NAICS sector 51 (Information)   
16  Number of jobs in NAICS sector 52 (Finance and...  
17  Number of jobs in NAICS sector 53 (Real Estate...  
18  Number of jobs in NAICS sector 54 (Professiona...  
19  Number of jobs in NAICS sector 55 (Management ...  
20  Number of jobs in NAICS sector 56 (Administrat...  
21  Number of jobs in NAICS sector 61 (Educational...  
22  Number of jobs in NAICS sector 62 (Health Care...  
23  Number of jobs in NAICS sector 71 (Arts, Enter...  
24  Number of jobs in NAICS sector 72 (Accommodati...  
25  Number of jobs in NAICS sector 81 (Other Servi...  
26  Number of jobs in NAICS sector 92 (Public Admi...  
27  Number of jobs for workers with Race: White, A...  
28  Number of jobs for workers with Race: Black or...  
29  Number of jobs for workers with Race: American...  
30  Numbe